In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/test-data/test.csv
/kaggle/input/vision_transformer/pytorch/v1/1/vit_price_regression.pth
/kaggle/input/vit-processed-test-data/VIT_test_subset.csv
/kaggle/input/test-zipped-images-vit/test_images/train_28241_71WXTPehhxL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_72455_719MCjs7hPL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_3614_71fmX7xzWlL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_61739_81H7BiOXQaL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_36675_81Bsxfa0s4L.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_53352_71xdEfATfJL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_57582_51bOzIDaxxL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_53127_81qZGmB5bfL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_34419_81nitcExBnL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_59262_81WSi9hnlqL.jpg
/kaggle/input/test-zipped-images-vit/test_images/train_29037_71U4BZiI

In [2]:
import os
import zipfile
import pandas as pd
from PIL import Image
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import torchvision.transforms as transforms
from transformers import ViTModel

2025-10-13 04:54:04.365960: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1760331244.560324      37 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1760331244.613630      37 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [3]:
# # ==========================
# # DATASET FOR TEST IMAGES FROM ZIP
# # ==========================
# class TestPriceDataset(Dataset):
#     """
#     Dataset for test images stored in a directory.
#     Expects a CSV with columns: sample_id, train_image_name
#     """
#     def __init__(self, csv_path, img_dir, transform=None, cache_dir="image_cache", sample_size=None):
#         self.df = pd.read_csv(csv_path)
#         if sample_size is not None:
#             self.df = self.df.head(sample_size)  # Limit to sample_size rows
#         self.img_dir = img_dir
#         self.transform = transform
#         self.cache_dir = cache_dir
#         os.makedirs(cache_dir, exist_ok=True)

#     def __len__(self):
#         return len(self.df)

#     def __getitem__(self, idx):
#         row = self.df.iloc[idx]
#         image_name = row["train_image_name"]
#         sample_id = row["sample_id"]
#         fname = os.path.join(self.cache_dir, f"{sample_id}.jpg")  # Cache by sample_id
#         if not os.path.exists(fname):
#             img_path = os.path.join(self.img_dir, image_name)
#             img = Image.open(img_path).convert("RGB")
#             img.save(fname)
#         else:
#             img = Image.open(fname).convert("RGB")
#         if self.transform:
#             img = self.transform(img)
#         return img, sample_id  # Return sample_id for mapping

In [4]:
# # ==========================
# # VISION TRANSFORMER REGRESSION MODEL
# # ==========================
# class ViTRegressionModel(nn.Module):
#     def __init__(self,
#                  model_name='google/vit-base-patch16-224',
#                  num_outputs=1,
#                  freeze_backbone=False,
#                  dropout_rate=0.1):
#         super().__init__()
#         self.vit = ViTModel.from_pretrained(model_name)
#         if freeze_backbone:
#             for p in self.vit.parameters():
#                 p.requires_grad = False
#         hidden_size = self.vit.config.hidden_size
#         self.reg_head = nn.Sequential(
#             nn.Dropout(dropout_rate),
#             nn.Linear(hidden_size, hidden_size // 2),
#             nn.ReLU(),
#             nn.Dropout(dropout_rate),
#             nn.Linear(hidden_size // 2, num_outputs)
#         )
#     def forward(self, pixel_values):
#         out = self.vit(pixel_values=pixel_values)
#         cls_feat = out.last_hidden_state[:, 0, :]
#         return self.reg_head(cls_feat)


In [5]:
# # ==========================
# # PREDICTION FUNCTION
# # ==========================
# def predict_prices(model, loader, device):
#     model.eval()
#     predictions = {}
#     with torch.no_grad():
#         for imgs, sample_ids in loader:
#             imgs = imgs.to(device)
#             pred = model(imgs).cpu().numpy().squeeze()
#             for sample_id, price in zip(sample_ids, pred):
#                 predictions[sample_id] = price
#     return predictions

In [6]:
# ==========================
# MAIN SCRIPT
# ==========================
/
    # print("Loading test dataset...")
    # # Dataset & DataLoader
    # test_dataset = TestPriceDataset(TEST_CSV_PATH, TEST_IMG_DIR, transform=transform)
    # print(f"Test dataset loaded with {len(test_dataset)} samples.")
    # test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False)
    # print("Test data loader created.")
    # # Load model
    # device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    # print(f"Using device: {device}")
    # model = ViTRegressionModel(freeze_backbone=False)
    # model.load_state_dict(torch.load(MODEL_PATH, map_location=device))
    # model.to(device)
    # print("Model loaded successfully.")
    # # Predict prices
    # print("Starting price prediction...")
    # predictions = predict_prices(model, test_loader, device)
    # print("Prediction completed.")
    # # Load CSV and update with predictions
    # print("Updating CSV with predicted prices...")
    # test_df = pd.read_csv(TEST_CSV_PATH)
    # test_df["predicted_price"] = test_df["sample_id"].map(predictions)
    # test_df.to_csv("/kaggle/working/test_data_with_predictions.csv", index=False)
    # print("CSV updated and saved to /kaggle/working/test_data_with_predictions.csv")

()

In [7]:
# if __name__ == "__main__":
#     TEST_CSV_PATH = "/kaggle/input/vit-processed-test-data/VIT_test_subset.csv"  # Path to test CSV
#     TEST_IMG_DIR = "/kaggle/input/test-zipped-images-vit/test_images"  # Path to test image directory
#     MODEL_PATH = "/kaggle/input/vision_transformer/pytorch/v1/1/vit_price_regression.pth"  # Path to saved model
#     SAMPLE_SIZE = 10  # Number of sample images to test
#     BATCH_SIZE = 16
#     IMG_SIZE = 224
#     # Transforms
#     transform = transforms.Compose([
#         transforms.Resize((IMG_SIZE, IMG_SIZE)),
#         transforms.ToTensor(),
#         transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
#     ])
#     print("Loading sample test dataset...")
#     # Dataset & DataLoader
#     test_dataset = TestPriceDataset(TEST_CSV_PATH, TEST_IMG_DIR, transform=transform, sample_size=SAMPLE_SIZE)
#     print(f"Sample dataset loaded with {len(test_dataset)} samples.")
#     test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False)
#     print("Sample data loader created.")
#     # Load model
#     device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
#     print(f"Using device: {device}")
#     model = ViTRegressionModel(freeze_backbone=False)
#     state_dict = torch.load(MODEL_PATH, map_location=device)
#     model.load_state_dict(state_dict)
#     model.to(device)
#     print("Model loaded successfully.")
#     # Predict prices for sample
#     print("Starting price prediction for sample images...")
#     predictions = predict_prices(model, test_loader, device)
#     print(f"Predictions dictionary size: {len(predictions)}")
#     print(f"Sample predictions: {dict(list(predictions.items())[:5])}")  # Show all predictions
#     # Optional: Verify with CSV mapping
#     test_df = pd.read_csv(TEST_CSV_PATH).head(SAMPLE_SIZE)
#     test_df["predicted_price"] = test_df["sample_id"].map(predictions)
#     print("Sample CSV with predictions:")
#     print(test_df[["sample_id", "train_image_name", "predicted_price"]])

In [8]:
class TestPriceDataset(Dataset):
    """
    Dataset for test images stored in a directory.
    Expects a CSV with columns: sample_id, train_image_name
    """
    def __init__(self, csv_path, img_dir, transform=None, cache_dir="image_cache", sample_size=None):
        self.df = pd.read_csv(csv_path)
        if sample_size is not None:
            self.df = self.df.head(sample_size)
        self.img_dir = img_dir
        self.transform = transform
        self.cache_dir = cache_dir
        os.makedirs(cache_dir, exist_ok=True)

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        image_name = row["train_image_name"]
        sample_id = row["sample_id"]

        # Cache image to avoid repeated I/O
        fname = os.path.join(self.cache_dir, f"{sample_id}.jpg")
        if not os.path.exists(fname):
            img_path = os.path.join(self.img_dir, image_name)
            img = Image.open(img_path).convert("RGB")
            img.save(fname)
        else:
            img = Image.open(fname).convert("RGB")

        if self.transform:
            img = self.transform(img)

        return img, sample_id


In [9]:
# VISION TRANSFORMER REGRESSION MODEL
class ViTRegressionModel(nn.Module):
    def __init__(self, model_name="google/vit-base-patch16-224", num_outputs=1,
                 freeze_backbone=False, dropout_rate=0.1):
        super().__init__()
        self.vit = ViTModel.from_pretrained(model_name)

        if freeze_backbone:
            for p in self.vit.parameters():
                p.requires_grad = False

        hidden_size = self.vit.config.hidden_size
        self.reg_head = nn.Sequential(
            nn.Dropout(dropout_rate),
            nn.Linear(hidden_size, hidden_size // 2),
            nn.ReLU(),
            nn.Dropout(dropout_rate),
            nn.Linear(hidden_size // 2, num_outputs)
        )

    def forward(self, pixel_values):
        out = self.vit(pixel_values=pixel_values)
        cls_feat = out.last_hidden_state[:, 0, :]
        return self.reg_head(cls_feat)

In [10]:
# IMPROVED PREDICTION FUNCTION
def predict_prices(model, loader, device):
    """
    Predict prices and return dictionary with integer keys.
    """
    model.eval()
    predictions = {}
    total_batches = len(loader)
    batch_count = 0

    with torch.no_grad():
        for imgs, sample_ids in loader:
            batch_count += 1
            print(f"Processing batch {batch_count}/{total_batches}")
            imgs = imgs.to(device)
            pred = model(imgs).cpu().numpy().squeeze()

            # Ensure iterable
            if pred.ndim == 0:
                pred = [pred.item()]

            for sid, price in zip(sample_ids, pred):
                # Convert tensor to int
                if isinstance(sid, torch.Tensor):
                    key = sid.item()
                else:
                    key = int(sid)
                predictions[key] = float(price)

    print(f"Generated {len(predictions)} predictions")
    return predictions

In [11]:
def process_full_dataset(csv_path, img_dir, model_path,
                         output_path="test_data_with_predictions.csv",
                         batch_size=16, img_size=224):
    """
    Process the entire test dataset and save predictions.
    """
    transform = transforms.Compose([
        transforms.Resize((img_size, img_size)),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406],
                             [0.229, 0.224, 0.225])
    ])

    print("Loading full test dataset...")
    test_dataset = TestPriceDataset(csv_path, img_dir, transform=transform)
    print(f"Full dataset loaded with {len(test_dataset)} samples.")

    test_loader = DataLoader(test_dataset, batch_size=batch_size,
                             shuffle=False, num_workers=2)
    print("Data loader created.")

    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    print(f"Using device: {device}")

    model = ViTRegressionModel(freeze_backbone=False)
    state_dict = torch.load(model_path, map_location=device)
    model.load_state_dict(state_dict)
    model.to(device)
    print("Model loaded successfully.")

    print("Starting price prediction for full dataset...")
    predictions = predict_prices(model, test_loader, device)

    print("Updating CSV with predicted prices...")
    df = pd.read_csv(csv_path)
    df["predicted_price"] = df["sample_id"].map(predictions)

    missing = df["predicted_price"].isna().sum()
    if missing > 0:
        print(f"Warning: {missing} samples missing predictions!")
    else:
        print("All samples have predictions!")

    df.to_csv(output_path, index=False)
    print(f"CSV saved to {output_path}")

    print("\nPrediction Statistics:")
    print(f"Total samples: {len(df)}")
    print(f"Successful predictions: {len(df) - missing}")
    print(f"Mean price: ${df['predicted_price'].mean():.2f}")
    print(f"Price range: ${df['predicted_price'].min():.2f} - ${df['predicted_price'].max():.2f}")


In [12]:
def test_sample_predictions(csv_path, img_dir, model_path,
                            sample_size=10, batch_size=16, img_size=224):
    """
    Test predictions on a small sample first.
    """
    transform = transforms.Compose([
        transforms.Resize((img_size, img_size)),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406],
                             [0.229, 0.224, 0.225])
    ])

    print("Loading sample test dataset...")
    ds = TestPriceDataset(csv_path, img_dir, transform=transform,
                          sample_size=sample_size)
    print(f"Sample dataset with {len(ds)} samples.")

    loader = DataLoader(ds, batch_size=batch_size, shuffle=False)
    print("Sample data loader created.")

    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    print(f"Using device: {device}")

    model = ViTRegressionModel(freeze_backbone=False)
    state_dict = torch.load(model_path, map_location=device)
    model.load_state_dict(state_dict)
    model.to(device)
    print("Model loaded successfully.")

    print("Starting price prediction for sample images...")
    preds = predict_prices(model, loader, device)

    print(f"Predictions size: {len(preds)}")
    print("First 5 predictions:")
    for i, (k, v) in enumerate(preds.items()):
        if i == 5: break
        print(f"  Sample {k}: ${v:.2f}")

    df = pd.read_csv(csv_path).head(sample_size)
    df["predicted_price"] = df["sample_id"].map(preds)
    print("\nSample CSV with predictions:")
    print(df[["sample_id", "train_image_name", "predicted_price"]])

    nan_count = df["predicted_price"].isna().sum()
    if nan_count > 0:
        print(f"\nWARNING: {nan_count}/{sample_size} predictions are NaN.")
    else:
        print(f"\nSUCCESS: All {sample_size} predictions valid.")

    return df

In [13]:
if __name__ == "__main__":
    TEST_CSV_PATH = "/kaggle/input/vit-processed-test-data/VIT_test_subset.csv"
    TEST_IMG_DIR = "/kaggle/input/test-zipped-images-vit/test_images"
    MODEL_PATH = "/kaggle/input/vision_transformer/pytorch/v1/1/vit_price_regression.pth"

    print("="*50)
    print("TESTING WITH SAMPLE DATA")
    print("="*50)
    sample_results = test_sample_predictions(
        csv_path=TEST_CSV_PATH,
        img_dir=TEST_IMG_DIR,
        model_path=MODEL_PATH,
        sample_size=10
    )

    if sample_results["predicted_price"].isna().sum() == 0:
        print("\n" + "="*50)
        print("PROCESSING FULL DATASET")
        print("="*50)
        process_full_dataset(
            csv_path=TEST_CSV_PATH,
            img_dir=TEST_IMG_DIR,
            model_path=MODEL_PATH,
            output_path="/kaggle/working/test_data_with_predictions.csv"
        )
    else:
        print(f"\nSample test failed with NaN values. Check mappings and data types.")

TESTING WITH SAMPLE DATA
Loading sample test dataset...
Sample dataset with 10 samples.
Sample data loader created.
Using device: cuda


config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/346M [00:00<?, ?B/s]

Some weights of ViTModel were not initialized from the model checkpoint at google/vit-base-patch16-224 and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Model loaded successfully.
Starting price prediction for sample images...
Processing batch 1/1
Generated 10 predictions
Predictions size: 10
First 5 predictions:
  Sample 100179: $17.88
  Sample 245611: $23.53
  Sample 146263: $20.71
  Sample 95658: $18.57
  Sample 36806: $19.42

Sample CSV with predictions:
   sample_id          train_image_name  predicted_price
0     100179   train_1_71hoAn78AWL.jpg        17.881577
1     245611   train_2_61ex8NHCIjL.jpg        23.525719
2     146263   train_3_61KCM61J8eL.jpg        20.706072
3      95658   train_4_51Ex6uOH7yL.jpg        18.565645
4      36806   train_5_71QYlrOMoSL.jpg        19.423359
5     148239   train_6_81ONUU3OAfL.jpg        14.859663
6      92659   train_7_519Plng8cpL.jpg        16.633881
7       3780   train_8_6134TQBo+vL.jpg        18.421251
8     196940   train_9_41bK3vFt5RL.jpg        20.237154
9      20472  train_10_81NWfSFYXBL.jpg        18.058046

SUCCESS: All 10 predictions valid.

PROCESSING FULL DATASET
Loading full 

Some weights of ViTModel were not initialized from the model checkpoint at google/vit-base-patch16-224 and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Model loaded successfully.
Starting price prediction for full dataset...
Processing batch 1/4688
Processing batch 2/4688
Processing batch 3/4688
Processing batch 4/4688
Processing batch 5/4688
Processing batch 6/4688
Processing batch 7/4688
Processing batch 8/4688
Processing batch 9/4688
Processing batch 10/4688
Processing batch 11/4688
Processing batch 12/4688
Processing batch 13/4688
Processing batch 14/4688
Processing batch 15/4688
Processing batch 16/4688
Processing batch 17/4688
Processing batch 18/4688
Processing batch 19/4688
Processing batch 20/4688
Processing batch 21/4688
Processing batch 22/4688
Processing batch 23/4688
Processing batch 24/4688
Processing batch 25/4688
Processing batch 26/4688
Processing batch 27/4688
Processing batch 28/4688
Processing batch 29/4688
Processing batch 30/4688
Processing batch 31/4688
Processing batch 32/4688
Processing batch 33/4688
Processing batch 34/4688
Processing batch 35/4688
Processing batch 36/4688
Processing batch 37/4688
Processing 